In [ ]:
!export PATH=/usr/local/cuda-10.1/bin:$PATH
!export LD_LIBRARY_PATH=/usr/local/cuda-10.1/lib64:$LD_LIBRARY_PATH
!pip install torch==1.6.0+cu101 torchvision==0.7.0+cu101 -f https://download.pytorch.org/whl/torch_stable.html

In [1]:
import sys,os,os.path

os.environ['PATH']="/usr/local/cuda-10.1/bin:$PATH"
os.environ['LD_LIBRARY_PATH']="/usr/local/cuda-10.1/lib64:$LD_LIBRARY_PATH"


In [2]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2019 NVIDIA Corporation
Built on Sun_Jul_28_19:07:16_PDT_2019
Cuda compilation tools, release 10.1, V10.1.243


In [3]:
import optuna
import torch.optim as optim
import joblib

/mnt/ds3lab-scratch/raox/gatech_data_cleaning/ICDE2021-revision/nacl36/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)
/mnt/ds3lab-scratch/raox/gatech_data_cleaning/ICDE2021-revision/nacl36/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


In [4]:
from optuna.cli import _Studies
from optuna.exceptions import CLIUsageError
from optuna.storages._base import DEFAULT_STUDY_NAME_PREFIX
from optuna.storages import RDBStorage
from optuna.study import StudyDirection
from optuna.testing.storage import StorageSupplier
from optuna.trial import Trial, FixedTrial

In [27]:
import sys
sys.setrecursionlimit(10**6)
import pickle
import os
import json
import numpy as np
from sklearn.metrics import f1_score
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.neural_network import MLPClassifier
from cleanlab.classification import LearningWithNoisyLabels
from sklearn.linear_model import LogisticRegression
from dataload import *
import operator

In [28]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.data as utils_data
from torch.autograd import Variable


In [29]:
data_dir = "../../CleanML/data-robustml-mv"
save_dir = "../../CleanML/result-robustml/"


model_name = "MLP"

In [30]:
error_type = 'missing_values'

In [31]:
jobs = get_jobs(data_dir, error_type = error_type, dataset = ['BabyProduct', 'Airbnb', 'Credit', 'Marketing', 'USCensus', 'Titanic'])

print(jobs)
print("Number of jobs:", len(jobs))

[['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_905', 'data.p'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_905', 'dirty_y_test.csv'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_905', 'dirty_y_train.csv'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_905', 'dirty_X_test.csv'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_905', 'dirty_X_train.csv'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_3462', 'dirty_y_test.csv'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_3462', 'dirty_X_train.csv'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_3462', 'data.p'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_3462', 'dirty_X_test.csv'], ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_3462', 'dirty_y_tra


Number of jobs: 600


In [32]:
class MLP(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(MLP, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.fc2 = nn.Linear(hidden_size, output_size)

    def forward(self, x):
        out = self.fc2(F.relu(self.fc1(x)))
        return out

In [33]:
torch.cuda.is_available()

True

In [34]:
dev = "cuda:4"

dev = "cpu"

In [35]:
def data_loader(data, train_batch_size, test_batch_size):
    #X_train, y_train = data["train"]
    X_train, y_train = data['train']['nacl']
    
    X_train = Variable(torch.Tensor(X_train)).to(dev)
    #print('X_train:', X_train, X_train.shape)
    y_train = Variable(torch.LongTensor(y_train)).to(dev)
    #print('y_train:', y_train, y_train.shape)

    #X_valid = X_train[:int(X_train.shape[0] * 0.2), :]
    
    #y_valid = y_train[:int(y_train.shape[0] * 0.2)]
    
    #X_train = X_train[X_valid.shape[0]:, :]
    #y_train = y_train[y_valid.shape[0]:]

    
    
    training_samples = utils_data.TensorDataset(X_train, y_train)
    data_loader_trn = utils_data.DataLoader(training_samples, batch_size=128, drop_last=False, shuffle=True)
    
    #valid_samples = utils_data.TensorDataset(X_valid, y_valid)
    #data_loader_vld = utils_data.DataLoader(valid_samples, batch_size=128, drop_last=False, shuffle=True)
    
    #X_test, y_test = data["test"]["dirty"]
    X_test, y_test = data["test"]['nacl']
        

    X_test = Variable(torch.Tensor(X_test)).to(dev)
    y_test = Variable(torch.Tensor(y_test)).to(dev)

    #print('X_test:', X_test, X_test.shape)
    #print('y_test:', y_test, y_test.shape)

    testing_samples = utils_data.TensorDataset(X_test, y_test)
    data_loader_tst = utils_data.DataLoader(testing_samples, batch_size=test_batch_size, 
                                            drop_last=False, shuffle=True)

    return data_loader_trn, data_loader_tst

In [36]:
def train(log_interval, model, train_loader, optimizer, epoch):
    
 
    # Generate the model.
    #print('model summary:', model)

    criterion = nn.MSELoss()
    
    # Training of the model.

    model.train()
    cum_loss = 0
    for batch_idx, (datat, target) in enumerate(train_loader):

        tr_x, tr_y = datat.float(), target.float()

        pred = model(tr_x.to(dev))
        #print('pred:', pred, type(pred), pred.shape)
        #print('tr_y:', tr_y.long(), type(tr_y.long()), tr_y.long().shape)

        loss = criterion(pred, tr_y.unsqueeze(1).to(dev))         

        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

    if batch_idx % log_interval == 0:
          print('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(
                epoch, batch_idx * len(data), len(train_loader.dataset),
                100. * batch_idx / len(train_loader), loss.item()))  
            
            

In [22]:
def test(model, test_loader):
    
    criterion = nn.MSELoss()

    # Validation of the model.
    model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        for datav, targetv in test_loader:
            
            output = model(datav.to(dev))
            test_loss += criterion(output, targetv.unsqueeze(1).to(dev)).item()  # sum up batch loss
            
            # Get the index of the max log-probability.
            preds = (output>0.5).float().squeeze(1)
            preds = preds.cpu().detach().numpy()

            ### END

            test_f1 = f1_score(targetv.cpu().detach().numpy(), preds, average='macro')
            test_acc = np.average(preds == targetv.cpu().detach().numpy())
            print('f1 and acc:', test_f1, test_acc)
            
            

    
    return test_acc





In [23]:
def train_data(trial):

    cfg = { 'device' : "cuda" if torch.cuda.is_available() else "cpu",
          'train_batch_size' : 128,
          'test_batch_size' : 1000,
          'n_epochs' : 100,
          'seed' : 0,
          'log_interval' : 100,
          'save_model' : False,
          'lr' : trial.suggest_loguniform('lr', 1e-5, 1e-2),          
          'momentum': trial.suggest_uniform('momentum', 0.4, 0.99),
          'optimizer': trial.suggest_categorical('optimizer',[optim.SGD, optim.RMSprop]),
          'activation': F.relu,
          'hidden_size': trial.suggest_int("hidden", 64, 128),
          'output_size': 1}

    torch.manual_seed(cfg['seed'])
    train_loader, test_loader = data_loader(data, cfg['train_batch_size'], cfg['test_batch_size'])
    
    for d, l in train_loader:
        input_size = d.shape[1]
        break
    #print('input_size:', input_size)
    model = MLP(input_size, cfg['hidden_size'], cfg['output_size']).to(dev)
    optimizer = cfg['optimizer'](model.parameters(), lr=cfg['lr'])

    for epoch in range(1, cfg['n_epochs'] + 1):
        train(cfg['log_interval'], model, train_loader, optimizer, epoch)
        test_accuracy = test(model, test_loader)
        print('test_acc:', test_accuracy)#, 'test_f1:', test_f1)
    if cfg['save_model']:
        torch.save(model.state_dict(), "test.pt")

    return test_accuracy

    

In [24]:
from dataload import *

In [37]:
if __name__ == '__main__':
    
    
    for job in jobs:
        if job[-1].endswith('.p'):
            print("Processing", job)
            dataset = job[1]
            result_dict = {}

            data = load_data(job)

            sampler = optuna.samplers.TPESampler()

            study = optuna.create_study(sampler=sampler, direction='maximize')
            study.optimize(func=train_data, n_trials=2)
            joblib.dump(study, '{}_optuna.pkl'.format(error_type))

            print("Best trial:")
            trial = study.best_trial

            print("  Value: ", trial.value)

            best_params = trial.params
            print("  Params: ")
            for key, value in best_params.items():
                print("    {}: {} ".format(key, value))

            best_params['optimizer'] = str(best_params['optimizer']).split('.')[-1].rstrip('\'>')

            result_dict["{}_test_f1".format('dirty')] = trial.value
            result_dict["{}_test_acc".format('dirty')] = trial.value
            result_dict["best_params"] = best_params

            print(result_dict)
            save_result_mv_dl(job, '3659', result_dict, model_name, save_dir)
        
    
    

Processing ['../../CleanML/data-robustml-mv', 'BabyProduct', 'missing_values', 'split_905', 'data.p']
f1 and acc: 0.29958988033957235 0.336
f1 and acc: 0.26875202674050236 0.3024390243902439
test_acc: 0.3024390243902439
f1 and acc: 0.28359027177885576 0.31
f1 and acc: 0.3774111466797997 0.4585365853658537
test_acc: 0.4585365853658537
f1 and acc: 0.3094148371431494 0.345
f1 and acc: 0.26106063598656926 0.28780487804878047
test_acc: 0.28780487804878047
f1 and acc: 0.29815243370385824 0.334
f1 and acc: 0.3281338557452996 0.35121951219512193
test_acc: 0.35121951219512193
f1 and acc: 0.30643127364438844 0.34
f1 and acc: 0.2958482676224612 0.32682926829268294
test_acc: 0.32682926829268294
f1 and acc: 0.30585911784068465 0.341
f1 and acc: 0.2978241048766664 0.32195121951219513
test_acc: 0.32195121951219513
f1 and acc: 0.2964797777253545 0.329
f1 and acc: 0.3445532589813952 0.3804878048780488
test_acc: 0.3804878048780488
f1 and acc: 0.2950155609863916 0.327
f1 and acc: 0.3584696143751262 0.395

test_acc: 0.4292682926829268
f1 and acc: 0.3533106786118835 0.372
f1 and acc: 0.3348024021697017 0.3463414634146341
test_acc: 0.3463414634146341
f1 and acc: 0.35697680170153834 0.376
f1 and acc: 0.3224203237713817 0.33170731707317075
test_acc: 0.33170731707317075
f1 and acc: 0.35706930587144886 0.375
f1 and acc: 0.323038073038073 0.33658536585365856
test_acc: 0.33658536585365856
f1 and acc: 0.36084172228572836 0.376
f1 and acc: 0.3024266660043218 0.33170731707317075
test_acc: 0.33170731707317075
f1 and acc: 0.3505820651900702 0.367
f1 and acc: 0.3545848091302637 0.375609756097561
test_acc: 0.375609756097561
f1 and acc: 0.3600236298967423 0.376
f1 and acc: 0.33286843328684335 0.35121951219512193
test_acc: 0.35121951219512193
f1 and acc: 0.3715057981670973 0.388
f1 and acc: 0.28321678321678323 0.2975609756097561
test_acc: 0.2975609756097561
f1 and acc: 0.3501861296511914 0.366
f1 and acc: 0.3870098039215686 0.40487804878048783
test_acc: 0.40487804878048783
f1 and acc: 0.37103616387647603

[I 2020-09-02 14:17:53,522] Trial 0 finished with value: 0.36097560975609755 and parameters: {'lr': 0.00016215316804435057, 'momentum': 0.40913183320413216, 'optimizer': <class 'torch.optim.sgd.SGD'>, 'hidden': 70}. Best is trial 0 with value: 0.36097560975609755.


f1 and acc: 0.26437277532089315 0.318
f1 and acc: 0.28416233413517494 0.34146341463414637
test_acc: 0.34146341463414637
f1 and acc: 0.27234624676194086 0.325
f1 and acc: 0.26091181058068474 0.3121951219512195
test_acc: 0.3121951219512195
f1 and acc: 0.2693660840164725 0.318
f1 and acc: 0.304250208855472 0.36585365853658536
test_acc: 0.36585365853658536
f1 and acc: 0.2804710817133177 0.331
f1 and acc: 0.292943279373631 0.33170731707317075
test_acc: 0.33170731707317075
f1 and acc: 0.29895564542215913 0.339
f1 and acc: 0.3238129330844563 0.37073170731707317
test_acc: 0.37073170731707317
f1 and acc: 0.3286519267053355 0.367
f1 and acc: 0.2682926829268293 0.2975609756097561
test_acc: 0.2975609756097561
f1 and acc: 0.3223852040816326 0.354
f1 and acc: 0.32244632400780743 0.3804878048780488
test_acc: 0.3804878048780488
f1 and acc: 0.32839275001555135 0.363
f1 and acc: 0.3559678416821274 0.3804878048780488
test_acc: 0.3804878048780488
f1 and acc: 0.3483126965687247 0.379
f1 and acc: 0.34450019

[I 2020-09-02 14:18:07,068] Trial 1 finished with value: 0.6829268292682927 and parameters: {'lr': 2.9016813004305443e-05, 'momentum': 0.8920388577795129, 'optimizer': <class 'torch.optim.rmsprop.RMSprop'>, 'hidden': 117}. Best is trial 1 with value: 0.6829268292682927.


...

Best trial:
  Value:  0.6367041198501873
  Params: 
    lr: 0.0002770208310520912 
    momentum: 0.6656568676400622 
    optimizer: <class 'torch.optim.sgd.SGD'> 
    hidden: 69 
{'dirty_test_f1': 0.6367041198501873, 'dirty_test_acc': 0.6367041198501873, 'best_params': {'lr': 0.0002770208310520912, 'momentum': 0.6656568676400622, 'optimizer': 'SGD', 'hidden': 69}}
Processing ['../../CleanML/data-robustml-mv', 'Titanic', 'missing_values', 'split_2962', 'data.p']
f1 and acc: 0.3833718244803695 0.6217228464419475
test_acc: 0.6217228464419475
f1 and acc: 0.3833718244803695 0.6217228464419475
test_acc: 0.6217228464419475
f1 and acc: 0.3833718244803695 0.6217228464419475
test_acc: 0.6217228464419475
f1 and acc: 0.3819444444444445 0.6179775280898876
test_acc: 0.6179775280898876
f1 and acc: 0.3819444444444445 0.6179775280898876
test_acc: 0.6179775280898876
f1 and acc: 0.3819444444444445 0.6179775280898876
test_acc: 0.6179775280898876
f1 and acc: 0.3819444444444445 0.6179775280898876
test_acc: 

[I 2020-09-02 16:00:11,122] Trial 0 finished with value: 0.6629213483146067 and parameters: {'lr': 0.0004304557266012007, 'momentum': 0.652501821417191, 'optimizer': <class 'torch.optim.sgd.SGD'>, 'hidden': 87}. Best is trial 0 with value: 0.6629213483146067.


f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5376000615763548 0.6629213483146067
test_acc: 0.6629213483146067
f1 and acc: 0.5451622164800459 0.6666666666666666
test_acc: 0.6666666666666666
f1 and acc: 0.5526275704493526 0.6704119850187266
test_acc: 0.6704119850187266
f1 and acc: 0.5526275704493526 0.6704119850187266
te

[I 2020-09-02 16:00:14,865] Trial 1 finished with value: 0.651685393258427 and parameters: {'lr': 0.0002468396506453259, 'momentum': 0.5817936626931318, 'optimizer': <class 'torch.optim.sgd.SGD'>, 'hidden': 89}. Best is trial 0 with value: 0.6629213483146067.


Best trial:
  Value:  0.6629213483146067
  Params: 
    lr: 0.0004304557266012007 
    momentum: 0.652501821417191 
    optimizer: <class 'torch.optim.sgd.SGD'> 
    hidden: 87 
{'dirty_test_f1': 0.6629213483146067, 'dirty_test_acc': 0.6629213483146067, 'best_params': {'lr': 0.0004304557266012007, 'momentum': 0.652501821417191, 'optimizer': 'SGD', 'hidden': 87}}


In [22]:
import optuna
import joblib

study = joblib.load('{}_optuna.pkl'.format(error_type))


In [24]:
df = study.trials_dataframe()
df.tail(3)

number     value             datetime_start          datetime_complete  \
17      17  0.623482 2020-09-02 11:27:06.749589 2020-09-02 11:27:09.466821   
18      18  0.619433 2020-09-02 11:27:09.472664 2020-09-02 11:27:12.024831   
19      19  0.609312 2020-09-02 11:27:12.029952 2020-09-02 11:27:14.691575   

          duration  params_hidden  params_lr  params_momentum  \
17 00:00:02.717232            115   0.004575         0.800432   
18 00:00:02.552167            114   0.000868         0.835272   
19 00:00:02.661623            101   0.003781         0.799451   

                         params_optimizer     state  
17  <class 'torch.optim.rmsprop.RMSprop'>  COMPLETE  
18  <class 'torch.optim.rmsprop.RMSprop'>  COMPLETE  
19  <class 'torch.optim.rmsprop.RMSprop'>  COMPLETE